In [1]:
from elasticsearch import Elasticsearch

In [17]:
es =  Elasticsearch(['http://localhost:9200/'], http_auth=('elastic', 'PhuwiCnCTXV9a*HAiGK2'))

C:\Users\HP PC\AppData\Local\Temp\ipykernel_10664\1625225303.py:1: DeprecationWarning: The 'http_auth' parameter is deprecated. Use 'basic_auth' or 'bearer_auth' parameters instead
  es =  Elasticsearch(['http://localhost:9200/'], http_auth=('elastic', 'PhuwiCnCTXV9a*HAiGK2'))


In [18]:
es.ping()

True

In [19]:
pip install pandas


  Using cached pandas-2.1.2-cp310-cp310-win_amd64.whl (10.7 MB)
  Using cached numpy-1.26.1-cp310-cp310-win_amd64.whl (15.8 MB)
  Using cached tzdata-2023.3-py2.py3-none-any.whl (341 kB)
  Using cached pytz-2023.3.post1-py2.py3-none-any.whl (502 kB)
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip available: 22.2.1 -> 23.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [29]:
import pandas as pd
df=pd.read_csv(r"C:\Users\HP PC\Desktop\nlp\bbc-news-data.csv", delimiter='\t').loc[:499]
df.head()

category filename                              title  \
0  business  001.txt  Ad sales boost Time Warner profit   
1  business  002.txt   Dollar gains on Greenspan speech   
2  business  003.txt  Yukos unit buyer faces loan claim   
3  business  004.txt  High fuel prices hit BA's profits   
4  business  005.txt  Pernod takeover talk lifts Domecq   

                                             content  
0   Quarterly profits at US media giant TimeWarne...  
1   The dollar has hit its highest level against ...  
2   The owners of embattled Russian oil giant Yuk...  
3   British Airways has blamed high fuel prices f...  
4   Shares in UK drinks and food firm Allied Dome...

In [37]:
df['filename'].info

<bound method Series.info of 0      001.txt
1      002.txt
2      003.txt
3      004.txt
4      005.txt
        ...   
495    496.txt
496    497.txt
497    498.txt
498    499.txt
499    500.txt
Name: filename, Length: 500, dtype: object>

In [31]:
df.isna().value_counts()

category  filename  title  content
False     False     False  False      500
Name: count, dtype: int64

In [34]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-mpnet-base-v2')

In [35]:
df['content_vector']=df['content'].apply(lambda x: model.encode(x))

In [38]:
df.head()

category filename                              title  \
0  business  001.txt  Ad sales boost Time Warner profit   
1  business  002.txt   Dollar gains on Greenspan speech   
2  business  003.txt  Yukos unit buyer faces loan claim   
3  business  004.txt  High fuel prices hit BA's profits   
4  business  005.txt  Pernod takeover talk lifts Domecq   

                                             content  \
0   Quarterly profits at US media giant TimeWarne...   
1   The dollar has hit its highest level against ...   
2   The owners of embattled Russian oil giant Yuk...   
3   British Airways has blamed high fuel prices f...   
4   Shares in UK drinks and food firm Allied Dome...   

                                      content_vector  
0  [0.014085239, 0.0659818, -0.0015852366, -0.014...  
1  [-0.050670415, 0.026130032, -0.019816918, -0.0...  
2  [0.084627226, 0.055390026, 0.011490086, -0.000...  
3  [-0.01655506, -0.018823108, -0.018902536, 0.01...  
4  [0.043643165, 0.064594366, 0.016669586, -0.006...

In [45]:
es.ping()

True

In [48]:
from iMapping import iMapping
es.indices.create(index="news",mappings=iMapping)

ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'news'})

In [49]:
record_list=df.to_dict("records")

In [50]:
record_list

[{'category': 'business',
  'filename': '001.txt',
  'title': 'Ad sales boost Time Warner profit',
  'content': ' Quarterly profits at US media giant TimeWarner jumped 76% to $1.13bn (£600m) for the three months to December, from $639m year-earlier.  The firm, which is now one of the biggest investors in Google, benefited from sales of high-speed internet connections and higher advert sales. TimeWarner said fourth quarter sales rose 2% to $11.1bn from $10.9bn. Its profits were buoyed by one-off gains which offset a profit dip at Warner Bros, and less users for AOL.  Time Warner said on Friday that it now owns 8% of search-engine Google. But its own internet business, AOL, had has mixed fortunes. It lost 464,000 subscribers in the fourth quarter profits were lower than in the preceding three quarters. However, the company said AOL\'s underlying profit before exceptional items rose 8% on the back of stronger internet advertising revenues. It hopes to increase subscribers by offering the 

In [51]:
for record in record_list:
    try:
        es.index(index="news",document=record,id=record['filename'])
    except Exception as e:
        print(e)

In [52]:
es.count(index="news")

ObjectApiResponse({'count': 500, '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0}})

In [53]:
input_keyword="oil prices in US"
input_vector=model.encode(input_keyword)

query={
    "field":"content_vector",
    "query_vector":input_vector,
    "k":5,
    "num_candidates":500,


}

res=es.knn_search(index="news",knn=query,source=["title","content","category"])
res["hits"]["hits"]


C:\Users\HP PC\AppData\Local\Temp\ipykernel_10664\895681438.py:13: ElasticsearchWarning: The kNN search API has been replaced by the `knn` option in the search API.
  res=es.knn_search(index="news",knn=query,source=["title","content","category"])


[{'_index': 'news',
  '_id': '138.txt',
  '_score': 0.85803473,
  '_source': {'category': 'business',
   'title': 'Winter freeze keeps oil above $50',
   'content': ' Oil prices carried on rising on Wednesday after cold weather on both sides of the North Atlantic pushed US crude prices to four-month highs.  Freezing temperatures and heavy snowfalls took crude oil prices past $50 a barrel on Tuesday for the first time since November. Declines in the dollar have also contributed to the rising oil price. US crude was trading at $51.39 at 0710 GMT in Asian electronic trade on Wednesday. A barrel of US crude oil closed up $2.80 at $51.15 in New York on Tuesday. Opec members said on Tuesday that, given such high prices, the cartel saw no reason to cut its output.  Although below last year\'s peak of $55.67 a barrel, which was reached in October, prices are now well above 2004\'s average of $41.48. Brent crude also rose in London trading, adding $1.89 to $48.62 at the close.  Much of western 